Working jupyter to create function to create a list of aminoacids likely to be used for mutation

To Do's:
- iterate through cutoff-value from -0.05 to 0.05 in 0.005 or 0.01 steps
- or reintroduce the first_entry loop, in case no mutation was found to force a mutation (not sure how good)
- set maximum limit of mutations, or find a compromise (e.g. minimum amount of mutation for best increase)
- use best Mutant (meltPoint prediction)
- Iterate through mutations
    - Iterate and take out one mutation -> lowest decrease gets kicked-out
    - repeat until sign, drop in increae (e.g. 0.9*og-mut-meltpoint)

    - start from wt add one see effect, etc.

In [ ]:
def prot_mut(pdb_path, pdb_file, pqr_output_path, Deep_mut=True, iterations=1, cutoff_value = -3, threshhold = 10, seed = 0):
    #import functions
    from function import functional_aa
    from function import free_aa
    from function import AA2s4pred
     
    from function_mut import diff_weighted
    from function_mut import mutator_rand
    from function_mut import mutator_rational
    from function_mut import pos_corr, neg_corr, ideal_pos_value, ideal_neg_value, conserv_subst, non_conservative_substitutions
    
    from SPARC import SPARC
    
    from helper_function import Subst_reducer
    from helper_function import pdb2AA
    from helper_function import ArraySlice

    from heapq import heappop, heappush
    import heapq
    import warnings
    
   

    #extract protein features
    aa_list = pdb2AA(pdb_path, pdb_file)
    aa_locked = functional_aa(pdb_path, pdb_file, pqr_output_path)
    aa_free = free_aa(pdb_path, pdb_file, aa_locked)
    aa_str = ''.join(aa_list)
    free_AA_dict = {a: b for a, b in zip(aa_free[:,2], aa_free[:,1] )} # create dictionary from array the key is the absolute aminoacid position and value is the aminoacid
    sec_prediction = AA2s4pred('./data/s4pred', pqr_output_path, aa_str, pdb_file)
    possible_substitutions = Subst_reducer(sec_prediction, conserv_subst, free_AA_dict, seed = seed)

    #calculate WT deviations
    WT_dev_sum, WT_dev = diff_weighted(pos_corr, neg_corr, aa_list, ideal_pos_value, ideal_neg_value, sec_prediction)





    #randoly mutate protein (within given constraints), get top 10 mutations
    #!!!!ToDo: implement to get top 10 sequences which vary most from eachother / WT
    top_variations = []
    largest_variations = []
    heappush(top_variations, (WT_dev_sum, WT_dev, aa_str))  # Placeholder for lowest score
    heappush(largest_variations, (0, WT_dev, aa_str))  # Placeholder for largest variation
    
    Mut_seq_str = mutator_rand(aa_list, possible_substitutions, threshhold = threshhold, seed = seed)
    for Mut_prot in Mut_seq_str:
        Mut_dev_sum, Mut_dev = diff_weighted(pos_corr, neg_corr, Mut_prot, ideal_pos_value, ideal_neg_value, sec_prediction, sort = True)
        Str_dev = sum(c1 != c2 for c1, c2 in zip(''.join(Mut_prot), aa_str))

        #save the top 10 scores
        if len(top_variations) < 11:
            heappush(top_variations, (Mut_dev_sum, Mut_dev, Mut_prot)) 
                  
        elif Mut_dev_sum < top_variations[0][0]:
            heappush(top_variations, (Mut_dev_sum, Mut_dev, Mut_prot))
            heappop(top_variations)
        
        #saves top 10 largest variations
        if len(largest_variations) <11:
            heappush(largest_variations, (Str_dev, Mut_dev, Mut_prot))
        elif Str_dev > largest_variations[0][0]:
            heappush(largest_variations, (Str_dev, Mut_dev, Mut_prot))
            heappop(largest_variations)
            
    heappush(top_variations, (WT_dev_sum, WT_dev, aa_str))
    
    Random_creation = list(heapq.merge(top_variations, largest_variations))
    
    print('Random mutation finished')
    #define variables for iteration
    prev_Mut_prot_list = aa_list    
    prev_Mut_dev = WT_dev           
    aa_available = aa_free          
    
    #define variables for best protein
    best_Mut_prot_list = list(heappop(top_variations)[2])
    best_Mut_dev_sum = heappop(top_variations)[0]
    best_Mut_dev = heappop(top_variations)[1]
    best_aa_available = aa_available
    
    
    #collect top 5 best variations of rational improvement to calculate melt point
    top_top_variations = []
    heappush(top_top_variations, (WT_dev_sum, WT_dev, aa_str))
    
    #use top 10 mutated sequences and use rational improvement      
    best_iteration = 0 #(used to track how many iterations are necessary, currently ~2-3 seems best)
    for mut_seq in top_variations:
        prev_Mut_prot_list = list(mut_seq[2])
        prev_Mut_dev_sum = mut_seq[0]
        prev_Mut_dev = mut_seq[1]

        for k in range(iterations):
            Mut_prot_list, possible_mutations = mutator_rational(
                                                    AA_list = prev_Mut_prot_list, 
                                                    free_AA = aa_available, 
                                                    deviation = prev_Mut_dev,
                                                    pos_corr = pos_corr, 
                                                    neg_corr =  neg_corr, 
                                                    conserv_substitution = possible_substitutions,
                                                    ideal_pos_value = ideal_pos_value, 
                                                    ideal_neg_value = ideal_neg_value,
                                                    cutoff = cutoff_value,
                                                    sec_prediction = sec_prediction
                                                    ) #f_value = cutoff, calculates list of possible mutations
            
            Mut_dev_sum, Mut_dev = diff_weighted(pos_corr, neg_corr, Mut_prot_list, ideal_pos_value, ideal_neg_value, sec_prediction) # calculate deviation of mutated protein sequence
            
            if len(top_top_variations) < 6:
                heappush(top_top_variations, (Mut_dev_sum, Mut_dev, Mut_prot_list))
            elif Mut_dev_sum < top_top_variations[0][0]:
                heappush(top_top_variations, (Mut_dev_sum, Mut_dev, Mut_prot_list))
                heappop(top_top_variations)
                
            if abs(best_Mut_dev_sum) > abs(Mut_dev_sum):
                best_Mut_prot_list = Mut_prot_list
                best_Mut_dev_sum = Mut_dev_sum
                best_Mut_dev = Mut_dev  
                best_possible_mutations = possible_mutations #get list of best mutations (AA-POS-AA), depreciated, bcs random mutator doesn't output this
                best_iteration = str(k+1)
                #aa_available = ArraySlice(aa_available, possible_mutations) #updates available aminoacids, so that each aminoacid can only be mutated once
                
            elif Mut_dev[0][0] == prev_Mut_dev[0][0] and abs(Mut_dev[0][1]-prev_Mut_dev[0][1]) < 0.001:
                break
                
            #update variables for next iteration            
            prev_possible_mutations = possible_mutations    #list of mutations (AA-POS-AA) (prev_possible_mutations can be printed if needed)
            prev_Mut_prot_list = Mut_prot_list                        #Mutated protein as a list with one AA per entry
            prev_Mut_dev = Mut_dev
            prev_Mut_dev_sum = Mut_dev_sum
        
    #for top_hit in top_top_variations:
    #-------SPARC implementation missing--------#
    wt_sparc = SPARC(aa_str, pdb_file.split('-')[1], './data', './data/s4pred')
    best_temp = wt_sparc[0]
    wt_temp = wt_sparc[0]  
    best_SPARC = wt_sparc
    
    #select best mutation based on melt point
    for top in top_top_variations:
        top_SPARC = SPARC(''.join(top[2]), pdb_file.split('-')[1], './data', './data/s4pred')
        top_temp = top_SPARC[0]
        if top_SPARC[0] > best_temp:
            best_temp = top_SPARC[0]
            best_SPARC = top_SPARC
            best_Mut_prot_list = top[2]
            best_Mut_dev_sum = top[0]
            best_Mut_dev = top[1]
    
    
    Improvement = WT_dev_sum - best_Mut_dev_sum
    return [(wt_sparc, best_SPARC), (aa_list, best_Mut_prot_list), (WT_dev_sum, best_Mut_dev_sum)]

In [ ]:
print(Mutated_improvement['AF-P37948-F1.pdb'][2][0])
print(Mutated_improvement['AF-P37948-F1.pdb'][2][1])

In [55]:
import os
#os.chdir('../../')
os.getcwd()

'c:\\Users\\marik\\OneDrive - bwedu\\Uni HD\\FS 4\\Bioinfo\\topic04_02'

In [119]:
def mutation_decreaser(mut_temp, wt_temp, wt_protein, mut_protein, name, cutoff = 0.9, min_diff = 0):
    from function_mut import diff_weighted
    from function_mut import pos_corr, neg_corr, ideal_pos_value, ideal_neg_value
    from SPARC import SPARC
    from heapq import heappop, heappush, nlargest, heapify
    from function import AA2s4pred
    import os
    #diff_weighted(feature_pos, feature_neg, aa:str, ideal_pos:dict, ideal_neg:dict, sec_prediction, sort = True, sum_only = False):
    #define variables for iteration
    start_Tm_diff = mut_temp-wt_temp
    wt_str = ''.join(wt_protein)
    best_mut_str = ''.join(mut_protein)
    Tm_diff = start_Tm_diff
    print(wt_str)
    print(start_mut_str)
    Mutations_list = []

            
    
    sec_prediction = AA2s4pred('./data/s4pred', './data', wt_str, name)
    #os.remove(os.path.join('./data', f'{name}.fasta'))
    #os.remove(os.path.join('./data', f'{name}.fas'))
    
    wt_diff = diff_weighted(pos_corr, neg_corr, wt_str, ideal_pos_value, ideal_neg_value, sec_prediction, sum_only = True)
    start_mut_diff = diff_weighted(pos_corr, neg_corr, best_mut_str, ideal_pos_value, ideal_neg_value, sec_prediction, sum_only = True)
    mut_diff = start_mut_diff

    while Tm_diff >= start_Tm_diff * cutoff or Tm_diff >= min_diff:
        sorted_wt_screen = [(float('inf'), 'dummy')]
        for i in range(len(best_mut_str)):
            if best_mut_str[i] != wt_str[i]:
                mut_str = best_mut_str[:i] + wt_str[i] + best_mut_str[i+1:]
                mut_diff = diff_weighted(pos_corr, neg_corr, mut_str, ideal_pos_value, ideal_neg_value, sec_prediction, sum_only = True)
                heappush(sorted_wt_screen, (mut_diff, mut_str))
                print(f'Current str {mut_str}')
        print(sorted_wt_screen)
        best_mut_diff = heappop(sorted_wt_screen)[0]
        best_mut_str = heappop(sorted_wt_screen)[1]
        sparc_screen = SPARC(mut_str, name, './data', './data/s4pred')
        Tm_diff = sparc_screen[0][0] - wt_temp
        if best_mut_str == wt_str:
            break
    return (best_mut_str, best_mut_diff, sparc_screen[0][0])


In [116]:
wt_temp = float(Mutated_improvement['AF-P37948-F1.pdb'][0][0][0][0])
mut_temp = float(Mutated_improvement['AF-P37948-F1.pdb'][0][1][0][0])
print(wt_temp)
print(mut_temp)
wt_aa = Mutated_improvement['AF-P37948-F1.pdb'][1][0]
mut_aa =Mutated_improvement['AF-P37948-F1.pdb'][1][1]

test = mutation_decreaser(mut_temp, wt_temp, wt_aa, mut_aa, 'P37948')
print(test[2])
print(test[1])

46.243893769473424
86.33506397971671
MLNIFKPAPHIERLDDSKMDAAYKRLRLQVFIGIFIGYAGYYLLRKNFAFAIPYLQEQGFSKTELGLVLAAVSIAYGFSKFIMGMVSDRCNPRYFLATGLFLSAIVNILFVSMPWVTSSVTIMFIFMFINGWFQGMGWPPCGRTMAHWFSISERGTKMSIWNVAHNIGGGILAPLVTLGIAMFVTWKSVFFFPAIIAIIISFLIVLLVRDTPQSCGLPPIEEYRNDYPKHAFKNQEKELTTKEILFQYVLNNKFLWYIAFANVFVYFVRYGVVDWAPTYLTEAKGFSPEDSRWSYFLYEYAGIPGTILCGWISDRFFKSRRAPAGVLFMAGVFIAVLVYWLNPAGNPLVDNIALISIGFLIYGPVMLIGLQAIDLAPKKAAGTAAGLTGFFGYIGGSAFANAIMGFVVDRFNWNGGFIMLISSCILAIVFLALTWNTGKRAEHV
MLNLFKPALPLERLDDSKMDAAYKPLRPLLFIGIFLGYAGYYPPPKNFAFAIPYLQEQGFPKTEPGPLLAALPIAYGLSKFIMGMVSDRCNLRYFLATGLFLPALVNIPFLPMLLLTSPLTIMFLFMFLNGWFLGMGLLPCGRTMAPLFPLPERGTKMPLLNVAPNIGGGIPALPVTLGIAMFVTWKSVLLFLALIALIISFPLLLLVRDTPQPCGPLLIEEYRNDYLKPALKNLEKEPTTKELPLLYLPNNKLPLYLALANLLLYLLPYGLLDLALTYPTEAKGLPLEDPPLPYLPYEYAGLLGTLPCGLLPDPLLKPPPALAGLPLMAGLLLALPLYLPNLAGNLPLDNLAPLPLGLPLYGLLMPLGPQALDPALKKAAGTAAGPTGLLGYLGGPALANALMGLLLDPLNLNGGLLMPLPPCLPALLLPAPTLNTGKPAEPL
fasta file already exists ./data\P37948.fasta
fas file already exists
Cur

In [134]:
print(mut_temp)
print(test[2])
wt_str = ''.join(wt_aa)
Mutations = []
for i in range(len(wt_str)):
    if wt_str[i] != test[0][i]:
        Mutations.append(f'{i+1}')
print(Mutations)
print(len(Mutations))
print(test[0])
print('+'.join(Mutations))
print('\n')
or_mut = '4+9+10+11+25+28+29+30+36+43+44+45+61+65+67+68+72+73+78+92+103+105+109+111+112+114+115+116+119+120+125+129+134+138+139+147+148+150+151+152+159+160+161+165+172+174+175+190+191+193+195+198+203+204+205+214+217+218+219+228+230+232+235+239+244+245+246+247+249+250+254+255+256+258+260+263+264+265+267+268+269+272+273+275+277+280+286+287+288+291+292+293+294+296+297+303+304+307+308+311+312+313+315+316+317+319+320+321+323+326+327+328+332+333+334+336+337+338+340+341+343+347+348+349+352+354+355+356+357+359+360+361+364+365+367+368+370+373+375+377+387+390+391+394+397+399+403+406+407+408+410+411+413+417+418+420+421+422+423+425+426+428+429+430+431+433+435+440+443+444'
or_mut_list = list(or_mut.split('+'))
print(len(or_mut_list))
print(or_mut_list)
for entry in or_mut_list:
    for n in Mutations:
        if n.split('-')[1] == entry:
            or_mut_list.remove(entry)
print('+'.join(or_mut_list))
print(len(or_mut_list))

        

86.33506397971671
79.51761038268991
['9', '25', '29', '30', '45', '61', '68', '72', '73', '78', '92', '103', '111', '112', '114', '115', '116', '119', '120', '134', '138', '139', '148', '150', '152', '159', '161', '174', '190', '191', '193', '205', '214', '218', '219', '228', '232', '235', '244', '246', '247', '249', '254', '256', '258', '260', '263', '264', '267', '269', '277', '286', '287', '288', '292', '296', '303', '304', '307', '312', '316', '317', '320', '321', '323', '328', '333', '334', '343', '347', '352', '355', '357', '359', '361', '364', '368', '373', '377', '390', '391', '394', '399', '403', '406', '410', '411', '417', '418', '421', '425', '426', '428', '430', '440']
95
MLNIFKPALHIERLDDSKMDAAYKPLRLLLFIGIFIGYAGYYLLPKNFAFAIPYLQEQGFPKTELGLLLAALPIAYGLSKFIMGMVSDRCNLRYFLATGLFLPAIVNILFLPMLLLTSPLTIMFIFMFINGWFLGMGLLPCGRTMAHLFPIPERGTKMPILNVAHNIGGGILALLVTLGIAMFVTWKSVLLFLAIIAIIISFLILLLVRDTPQPCGLLLIEEYRNDYLKHALKNLEKELTTKELLLLYLLNNKLLLYLALANLLVYLVPYGVVDWALTYLTEAKGLPLEDSPWSYLLYEYAGLLGTL

IndexError: list index out of range

In [42]:
from SPARC import SPARC
mut_test = 'MLNIFKPALPLERLDDSKMDAAYKPLRPLLFIGIFLGYAGYYPPPKNFAFAIPYLQEQGFPKTEPGPLLAALPIAYGLSKFIMGMVSDRCNLRYFLATGLFLPALVNIPFLPMLLLTSPLTIMFLFMFLNGWFLGMGLLPCGRTMAPLFPLPERGTKMPLLNVAPNIGGGIPALPVTLGIAMFVTWKSVLLFLALIALIISFPLLLLVRDTPQPCGPLLIEEYRNDYLKPALKNLEKEPTTKELPLLYLPNNKLPLYLALANLLLYLLPYGLLDLALTYPTEAKGLPLEDPPLPYLPYEYAGLLGTLPCGLLPDPLLKPPPALAGLPLMAGLLLALPLYLPNLAGNLPLDNLAPLPLGLPLYGLLMPLGPQALDPALKKAAGTAAGPTGLLGYLGGPALANALMGLLLDPLNLNGGLLMPLPPCLPALLLPAPTLNTGKPAEPL'
test = SPARC(mut_aa, 'P37948', './data', './data/s4pred')
print(test[0][0])

86.33506397971671


Mutational screen of all esssential proteins

In [4]:
import pandas as pd
import os
data_path = './data/essential_proteins.csv'
ess_prot_AFdb = (
    pd.read_csv(data_path)['AlphaFoldDB']
    .dropna()  
    .str.replace(';', '')  
    .apply(lambda x: f'AF-{x}-F1.pdb') 
)
ess_prot_AFdb = ess_prot_AFdb.tolist()

path_pdb = './data/pdbs'
path_pqr=  './data/pqrs'
output_path = './data/test'

Mutator_dict = {}
count = 14
no_pdb = []
for entry in ess_prot_AFdb[13:]:
    if os.path.exists(os.path.join(path_pdb, entry)):
        Mutator_dict[entry] = prot_mut(path_pdb, entry, path_pqr, Deep_mut=True, iterations=100, cutoff_value = -0.005, threshhold = 1000, seed = 0)
        print(f'{entry} finished ({count}/{len(ess_prot_AFdb)})')
        count += 1
    else:
        no_pdb.append(entry)
        print(f'{os.path.join(path_pdb,entry)} not found')
        print


./data/pdbs\AF-O31776-F1.pdb not found
./data/pdbs\AF-O31777-F1.pdb not found


NameError: name 'prot_mut' is not defined

In [6]:
for protein in Mutated_improvement:
    Diff_diff = Mutated_improvement[protein][2][0] - Mutated_improvement[protein][2][1]
    print(f'{protein} Diff WT = {Mutated_improvement[protein][2][0]}; Diff Mut = {Mutated_improvement[protein][2][1]}; Diff WT-Mut = {Diff_diff}')

AF-O31914-F1.pdb Diff WT = 2.8118955314000553; Diff Mut = 2.84440291633584; Diff WT-Mut = -0.03250738493578487
AF-O32152-F1.pdb Diff WT = 3.1147268499512695; Diff Mut = 3.1564393932823065; Diff WT-Mut = -0.04171254333103702
AF-O34338-F1.pdb Diff WT = 3.180742226020291; Diff Mut = 3.5282909570483083; Diff WT-Mut = -0.3475487310280174
AF-O34453-F1.pdb Diff WT = 3.0349906815662147; Diff Mut = 3.0035306264697956; Diff WT-Mut = 0.031460055096419026
AF-O34748-F1.pdb Diff WT = 3.5973917107785027; Diff Mut = 3.3742465536231947; Diff WT-Mut = 0.22314515715530803
AF-O34798-F1.pdb Diff WT = 2.898619362064633; Diff Mut = 3.2333094986216047; Diff WT-Mut = -0.33469013655697166
AF-O35024-F1.pdb Diff WT = 3.312212882877846; Diff Mut = 3.32975788396221; Diff WT-Mut = -0.017545001084363854
AF-P00864-F1.pdb Diff WT = 3.5113610196170817; Diff Mut = 3.4851648637011605; Diff WT-Mut = 0.02619615591592117
AF-P03018-F1.pdb Diff WT = 3.9249369080840886; Diff Mut = 4.219852162321378; Diff WT-Mut = -0.29491525423

In [2]:
import pickle
with(open('./data/Essential_genes_mutated.pkl', 'rb')) as f:
    Mutator_dict_load = pickle.load(f)
with(open('./data/Mutator_dict_13first_bs_error.pkl', 'rb')) as f:
    Mutator_dict_13 = pickle.load(f)
Mutated_proteins = {**Mutator_dict_load, **Mutator_dict_13}
Increase = 0
No_improvement = []
Mutated_improvement = {}
for key in Mutated_proteins:
    if Mutated_proteins[key][0][0][0] == Mutated_proteins[key][0][1][0]:
        No_improvement.append(key)
    else:
        Mutated_improvement[key] = Mutated_proteins[key]

Diff = 0
Changed_aa_amount = 0
highest_increase = ('name',0)
biggest_relative_change = ('name',0)
biggest_absolute_chagne = ('name',0)
rel_mut_increase = ('name',0)
for key in Mutated_improvement:
    #Melt point increase
    Diff += float(Mutated_improvement[key][0][1][0][0]) - float(Mutated_improvement[key][0][0][0][0])
    
    #highest increase
    if float(Mutated_improvement[key][0][1][0][0]) - float(Mutated_improvement[key][0][0][0][0]) > highest_increase[1]:
        highest_increase = (key, float(Mutated_improvement[key][0][1][0][0]) - float(Mutated_improvement[key][0][0][0][0]))
    
    #percentage of changed aminoacids
    changed_aa = 0
    for n in range(len(Mutated_improvement[key][1][0])): 
        if Mutated_improvement[key][1][0][n] != Mutated_improvement[key][1][1][n]:
            changed_aa += 1
    if changed_aa/len(Mutated_improvement[key][1][0]) > biggest_relative_change[1]:
        biggest_relative_change = (key, changed_aa/len(Mutated_improvement[key][1][0]))
    if changed_aa > biggest_absolute_chagne[1]:
        biggest_absolute_chagne = (key, changed_aa)
    Changed_aa_amount += changed_aa/len(Mutated_improvement[key][1][0])
    if changed_aa > 0:
        if (float(Mutated_improvement[key][0][1][0][0]) - float(Mutated_improvement[key][0][0][0][0]))/float(changed_aa) > rel_mut_increase[1]:
            rel_mut_increase = (key, (float(Mutated_improvement[key][0][1][0][0]) - float(Mutated_improvement[key][0][0][0][0]))/float(changed_aa))

#Mutation list for edge cases
highest_increase_mut_list = []
biggest_rel_change_mut_list = []
biggest_abs_change_mut_list =[]
highest_mut2melt_list = []
for key in Mutated_improvement:
    if key == highest_increase[0]:
        for n in range(len(Mutated_improvement[key][1][0])):
            if Mutated_improvement[key][1][0][n] != Mutated_improvement[key][1][1][n]:
                highest_increase_mut_list.append(f'{n+1}')
    if key == biggest_relative_change[0]:
        for n in range(len(Mutated_improvement[key][1][0])):
            if Mutated_improvement[key][1][0][n] != Mutated_improvement[key][1][1][n]:
                biggest_rel_change_mut_list.append(f'{n+1}')
    if key == biggest_absolute_chagne[0]:
        for n in range(len(Mutated_improvement[key][1][0])):
            if Mutated_improvement[key][1][0][n] != Mutated_improvement[key][1][1][n]:
                biggest_abs_change_mut_list.append(f'{n+1}')
    if key == rel_mut_increase[0]:
        for n in range(len(Mutated_improvement[key][1][0])):
            if Mutated_improvement[key][1][0][n] != Mutated_improvement[key][1][1][n]:
                highest_mut2melt_list.append(f'{n+1}')


#Print results
#print(f'Proteins without a pdb file: {len(no_pdb)}')
print(f"Proteins that couldn't be improved: {len(No_improvement)}")
print(f'Proteins that could be improved: {len(Mutated_improvement.keys())} \n')
print(f'Average meltPoint increase: {Diff/len(Mutated_improvement.keys())}')
print(f'Average percentage of changed aminoacid per protein: {Changed_aa_amount/len(Mutated_improvement.keys())} \n')
print(f'Highest meltPoint increase: {highest_increase[0]} with {highest_increase[1]} ({Mutated_improvement[highest_increase[0]][0][0][0][0]} -> {Mutated_improvement[highest_increase[0]][0][1][0][0]})\nWT sequence:      {''.join(Mutated_improvement['AF-P37948-F1.pdb'][1][0])} \nMutated sequence: {''.join(Mutated_improvement['AF-P37948-F1.pdb'][1][1])}')
print(f'{'+'.join(highest_increase_mut_list)}\n')
print(f'Highest percentage of changed aminoacid: {biggest_relative_change[0]} with {biggest_relative_change[1]} with {int(len(Mutated_improvement[biggest_relative_change[0]][1][0])*biggest_relative_change[1])} of {len(Mutated_improvement[biggest_relative_change[0]][1][0])}\nWT sequence:      {''.join(Mutated_improvement['AF-Q47710-F1.pdb'][1][0])} \nMutated sequence: {''.join(Mutated_improvement['AF-Q47710-F1.pdb'][1][1])}')
print(f'{'+'.join(biggest_rel_change_mut_list)}\n')
print(f'Highest absolute number of changed aminoacid: {biggest_absolute_chagne[0]} with {biggest_absolute_chagne[1]} of {len(Mutated_improvement[biggest_absolute_chagne[0]][1][0])}\nWT sequence:      {''.join(Mutated_improvement['AF-P46918-F1.pdb'][1][0])} \nMutated sequence: {''.join(Mutated_improvement['AF-P46918-F1.pdb'][1][1])}')
print(f'{'+'.join(biggest_abs_change_mut_list)}\n')                                                                                                                                                                                                                                         
print(f'')
print(f'Biggest meltPoint change per mutation {rel_mut_increase[0]} with {rel_mut_increase[1]} ({Mutated_improvement[rel_mut_increase[0]][0][0][0][0]} -> {Mutated_improvement[rel_mut_increase[0]][0][1][0][0]})\nWT sequence:      {''.join(Mutated_improvement[rel_mut_increase[0]][1][0])} \nMutated sequence: {''.join(Mutated_improvement[rel_mut_increase[0]][1][1])}')
print(f'{'+'.join(highest_mut2melt_list)}\n')


Proteins that couldn't be improved: 12
Proteins that could be improved: 95 

Average meltPoint increase: 14.095511187453862
Average percentage of changed aminoacid per protein: 0.11285151198028498 

Highest meltPoint increase: AF-P37948-F1.pdb with 40.091170210243284 (46.243893769473424 -> 86.33506397971671)
WT sequence:      MLNIFKPAPHIERLDDSKMDAAYKRLRLQVFIGIFIGYAGYYLLRKNFAFAIPYLQEQGFSKTELGLVLAAVSIAYGFSKFIMGMVSDRCNPRYFLATGLFLSAIVNILFVSMPWVTSSVTIMFIFMFINGWFQGMGWPPCGRTMAHWFSISERGTKMSIWNVAHNIGGGILAPLVTLGIAMFVTWKSVFFFPAIIAIIISFLIVLLVRDTPQSCGLPPIEEYRNDYPKHAFKNQEKELTTKEILFQYVLNNKFLWYIAFANVFVYFVRYGVVDWAPTYLTEAKGFSPEDSRWSYFLYEYAGIPGTILCGWISDRFFKSRRAPAGVLFMAGVFIAVLVYWLNPAGNPLVDNIALISIGFLIYGPVMLIGLQAIDLAPKKAAGTAAGLTGFFGYIGGSAFANAIMGFVVDRFNWNGGFIMLISSCILAIVFLALTWNTGKRAEHV 
Mutated sequence: MLNLFKPALPLERLDDSKMDAAYKPLRPLLFIGIFLGYAGYYPPPKNFAFAIPYLQEQGFPKTEPGPLLAALPIAYGLSKFIMGMVSDRCNLRYFLATGLFLPALVNIPFLPMLLLTSPLTIMFLFMFLNGWFLGMGLLPCGRTMAPLFPLPERGTKMPLLNVAPNIGGGIPALPVTLGIAMFVTWKSVLLFLALIALIISFPLLLLV

Get list of pos/neg correlating features for Meltpoint

In [ ]:
import pandas as pd
import os
pro_df: pd.DataFrame = pd.read_csv(os.path.join('./data', 'prokaryotes_323columns.csv'))
pro_df = pro_df.drop(columns = ['Unnamed: 0', 'Unnamed: 0.1'])

In [ ]:
import numpy as np
top_df = pro_df[pro_df['meltPoint'] >= pro_df['meltPoint'].quantile(0.9)]
Ideal_pos_value = {}
Ideal_neg_value = {}

keys = ['Rhelix', 'Qhelix']
for key in keys:
    Ideal_pos_value[key] = np.mean(top_df[key])

""" for key in neg_corr.keys():
    Ideal_neg_value[key] = np.mean(top_df[key]) """
    
print(Ideal_pos_value)
print(Ideal_neg_value)


In [ ]:
pro_corr = pro_df.corr(numeric_only=True)['meltPoint']
pos_corr = pro_corr[pro_corr > 0.32]
neg_corr = pro_corr[pro_corr < -0.32]

In [ ]:
pos_corr = list(pro_corr.index)
neg_corr = list(neg_corr.index)
print(neg_corr)

Needs to be mutated

In [ ]:
print(pro_corr[pro_corr < -0.32])